In [1]:
import json
import math
import pickle
import random

from collections import Counter, defaultdict

from sklearn.feature_extraction.text import TfidfVectorizer
from skmultilearn.adapt import MLkNN
from skmultilearn.embedding import EmbeddingClassifier
from scipy.sparse import lil_matrix
from skmultilearn.embedding import OpenNetworkEmbedder
from skmultilearn.cluster import LabelCooccurrenceGraphBuilder
from skmultilearn.embedding import EmbeddingClassifier
from sklearn.ensemble import RandomForestRegressor
from skmultilearn.adapt import MLkNN

## Load data in raw format:

In [2]:
random.seed(41)
with open('tasks_info.json') as data_file:
    tasks = json.load(data_file)['result']['problems']
with open('extracted_meta.json') as meta_file:
    meta = json.load(meta_file)

In [3]:
all_tags = sorted(set(sum((task['tags'] for task in tasks), [])))
print(len(all_tags))
print(all_tags)

36
['*special', '2-sat', 'binary search', 'bitmasks', 'brute force', 'chinese remainder theorem', 'combinatorics', 'constructive algorithms', 'data structures', 'dfs and similar', 'divide and conquer', 'dp', 'dsu', 'expression parsing', 'fft', 'flows', 'games', 'geometry', 'graph matchings', 'graphs', 'greedy', 'hashing', 'implementation', 'math', 'matrices', 'meet-in-the-middle', 'number theory', 'probabilities', 'schedules', 'shortest paths', 'sortings', 'string suffix structures', 'strings', 'ternary search', 'trees', 'two pointers']


In [4]:
def normalize(variable):
    return variable.lower().replace('_', '')

In [5]:
word_counter = Counter()
for meta_item in meta.values():
    document_words = []
    for word_list in meta_item.values():
        for word in word_list:
            document_words.append(normalize(word))
    for word in set(document_words):
        word_counter[word] += 1
good_words = set(x for x in word_counter if word_counter[x] >= 3)
print(len(word_counter), len(good_words))

101786 28378


In [6]:
def transform_data(tasks, meta, all_tags):
    x = []
    y = []
    tasks_dict = {
        (str(value['contestId']), value['index']): value
        for value in tasks
    }
    
    for solution_path, value in meta.items():
        _, task_contest, task_index, _ = solution_path.split('/')
        task = tasks_dict[task_contest, task_index]
        tags = task['tags']
        if not tags:
            continue
        task_x = []
        for item_key in 'variables', 'function_names':
            for word in value[item_key]:
                if word in good_words:
                    task_x.append(normalize(word))
        if len(task_x) >= 5:  # remove?
            x.append(' '.join(task_x))
            y.append([int(tag in tags) for tag in all_tags])
    return x, y

In [7]:
x, y = transform_data(tasks, meta, all_tags)
permutation = list(range(len(x)))
random.shuffle(permutation)
x = [x[i] for i in permutation]
y = [y[i] for i in permutation]
TRAIN_PART = 0.9
border = int(TRAIN_PART * len(x))
x_train = x[:border]
y_train = y[:border]
x_test = x[border:]
y_test = y[border:]

Проанализируем, какие из слов характерны для каждого тега:

In [8]:
def tfidf(tag_meta):
    result = defaultdict(dict)
    idf = {}
    total = len(tag_meta)
    all_words = set(sum(tag_meta.values(), []))
    word_frequency = Counter(
        sum([list(set(x)) for x in tag_meta.values()], [])
    )
    for word in all_words:
        idf[word] = math.log(total * 1. / word_frequency[word])

    for tag in tag_meta:
        word_count = Counter(tag_meta[tag])
        tfidf = {}
        for word in word_count:
            tf = word_count[word]
            tfidf[word] = float(tf) * idf[word]

        result[tag] = sorted(tfidf.items(), key=lambda x: -x[1])
    return result, idf


def process(x_train, y_train, all_tags, debug=False):
    tag_meta = defaultdict(list)
    for cx, cy in zip(x_train, y_train):
        for tag, cy_item in zip(all_tags, cy):
            if cy_item:
                tag_meta[tag] += cx.split(' ')

    tfidf_scores, idf = tfidf(tag_meta)

    idf = sorted(idf.items(), key=lambda x: x[1])

    if debug:
        for tag in tag_meta:
            print('tag:', tag)

        for tag in tag_meta:
            print('tag:', tag)
            for ind, i in enumerate(tfidf_scores[tag]):
                if ind == 20:
                    break
                print(ind, i[1], i[0])
            print('\n')
    return tfidf_scores


In [9]:
process(x_train, y_train, all_tags, debug=True)

tag: data structures
tag: bitmasks
tag: combinatorics
tag: dp
tag: math
tag: brute force
tag: probabilities
tag: number theory
tag: divide and conquer
tag: matrices
tag: trees
tag: binary search
tag: greedy
tag: two pointers
tag: constructive algorithms
tag: dfs and similar
tag: geometry
tag: implementation
tag: sortings
tag: dsu
tag: graphs
tag: string suffix structures
tag: strings
tag: fft
tag: flows
tag: graph matchings
tag: expression parsing
tag: hashing
tag: shortest paths
tag: *special
tag: meet-in-the-middle
tag: games
tag: schedules
tag: ternary search
tag: chinese remainder theorem
tag: 2-sat
tag: data structures
0 822.7707272120932 lca
1 343.79474246672123 pushdown
2 247.7749956829843 lazy
3 235.16976270273534 lcp
4 225.73692524229998 pushup
5 217.54526685734024 dep
6 198.85412174918125 type
7 188.71943952836824 fen
8 179.9918451819982 push
9 168.705904729331 fib
10 168.56880342513728 tout
11 160.54733414188092 splay
12 138.69613492146973 dfs1
13 138.15188625115582 adj
14 1

defaultdict(dict,
            {'data structures': [('lca', 822.7707272120932),
              ('pushdown', 343.79474246672123),
              ('lazy', 247.7749956829843),
              ('lcp', 235.16976270273534),
              ('pushup', 225.73692524229998),
              ('dep', 217.54526685734024),
              ('type', 198.85412174918125),
              ('fen', 188.71943952836824),
              ('push', 179.9918451819982),
              ('fib', 168.705904729331),
              ('tout', 168.56880342513728),
              ('splay', 160.54733414188092),
              ('dfs1', 138.69613492146973),
              ('adj', 138.15188625115582),
              ('upd', 138.1218097677116),
              ('son', 134.27266064827714),
              ('access', 130.31166994526973),
              ('idom', 126.73023913918801),
              ('shift', 123.2141487920742),
              ('tin', 119.5713789837087),
              ('dfs2', 118.20359982101375),
              ('link', 113.04599088204866),
  

In [10]:
preprocessed_tags = [
    'binary search',
    'bitmasks',
]
partially_preprocessed_tags = [
    'string suffix structures',
    'hashing',
]
excluded_tags = [
    '*special',
    'brute force',
    'greedy',
    'implementation',
    'divide and conquer',
    'sortings',
    'meet-in-the-middle',
    'schedules',  # 5 tasks
]
all_tags = [tag for tag in all_tags if tag not in excluded_tags]

print(len(all_tags))
print(all_tags)

28
['2-sat', 'binary search', 'bitmasks', 'chinese remainder theorem', 'combinatorics', 'constructive algorithms', 'data structures', 'dfs and similar', 'dp', 'dsu', 'expression parsing', 'fft', 'flows', 'games', 'geometry', 'graph matchings', 'graphs', 'hashing', 'math', 'matrices', 'number theory', 'probabilities', 'shortest paths', 'string suffix structures', 'strings', 'ternary search', 'trees', 'two pointers']


Убрали теги, на который нет шансов на успех

In [11]:
with open('additional_tag_processing.txt') as meta_file:
    additional_tag_info = json.load(meta_file)

In [12]:
def transform_data_part(tasks, meta, all_tags, additional_tag_info):
    x = []
    y = []
    extra = []
    solution_info = []
    tasks_dict = {
        (str(value['contestId']), value['index']): value
        for value in tasks
    }
    
    for solution_path, value in meta.items():
        _, task_contest, task_index, _ = solution_path.split('/')
        
        curr_extra =[]
        if solution_path in additional_tag_info:
             curr_extra = additional_tag_info[solution_path]
        task = tasks_dict[task_contest, task_index]
        tags = [tag for tag in task['tags'] if tag in all_tags]
        if not tags:
            continue
        task_x = []
        for item_key in 'variables', 'function_names':
            for word in value[item_key]:
                if word in good_words:
                    task_x.append(normalize(word))
        if len(task_x) >= 5:  # remove?
            x.append(' '.join(task_x))
            y.append([int(tag in tags) for tag in all_tags])
            extra.append(curr_extra)
            solution_info.append(solution_path)
    return x, y, extra, solution_info

In [13]:
x, y, extra, solution_info = transform_data_part(tasks, meta, all_tags, additional_tag_info)
permutation = list(range(len(x)))
random.shuffle(permutation)
x = [x[i] for i in permutation]
y = [y[i] for i in permutation]
extra = [extra[i] for i in permutation]
solution_info = [solution_info[i] for i in permutation]
# no train/test here because there is no way to check quality
# TRAIN_PART = 0.9
# border = int(TRAIN_PART * len(x))
# x_train = x[:border]
# y_train = y[:border]
# extra_train = extra[:border]
# x_test = x[border:]
# y_test = y[border:]
# extra_test = extra[border:]

In [14]:
additional_tag_info

{'source_codes/850/C/30084276.cpp': ['bitmasks'],
 'source_codes/528/D/22462345.cpp': ['bitmasks'],
 'source_codes/356/D/4834649.cpp': ['bitmasks'],
 'source_codes/176/E/2875595.cpp': ['binary search'],
 'source_codes/713/B/20580004.cpp': ['binary search'],
 'source_codes/1042/D/52343288.cpp': ['bitmasks'],
 'source_codes/377/C/5639507.cpp': ['bitmasks'],
 'source_codes/596/E/14324562.cpp': ['bitmasks'],
 'source_codes/54/C/246534.cpp': ['binary search'],
 'source_codes/137/D/961166.cpp': ['binary search'],
 'source_codes/504/D/9512680.cpp': ['bitmasks'],
 'source_codes/1017/G/49199020.cpp': ['bitmasks'],
 'source_codes/557/E/11868611.cpp': ['string suffix structures'],
 'source_codes/161/C/1356442.cpp': ['bitmasks'],
 'source_codes/1109/B/50023107.cpp': ['bitmasks'],
 'source_codes/582/E/13383506.cpp': ['bitmasks'],
 'source_codes/756/C/24053931.cpp': ['bitmasks'],
 'source_codes/903/F/50721124.cpp': ['bitmasks'],
 'source_codes/842/D/29885766.cpp': ['bitmasks'],
 'source_codes/331/D3

In [15]:
def detect_string_suffix_structures(_x):
    keywords = [
        'alphabet', 
        'lcp',
        'saextend',
        'sainit'
        'invlink',
        'getlink',
        'treeextend',
        'buildsa',
        'sabuild',
        'kmp',
        'ahocorasick',
    ]
    for name in _x.split():
        if name in keywords:
            return True


def detect_hashing(_x):
    for name in _x.split():
        if name.startswith('hash') or name.endswith('hash'):
            return True
    return False


detection_mappings = {
    'string suffix structures': detect_string_suffix_structures,
    'hashing': detect_hashing,
}



def apply_detectors(x, _extra, all_tags):
    detected = []
    for _x, _extra in zip(x, extra):
        for tag in all_tags:
            if tag in preprocessed_tags:
                if tag in extra:
                    detected.append(tag)
            elif tag in partially_preprocessed_tags:
                if tag in extra:
                    detected.append(tag)
                else:
                    if detection_mappings[tag](_x):
                        detected.append(tag)

In [16]:
tfidf_scores = process(x, y, all_tags)
print(tfidf_scores.keys())

dict_keys(['combinatorics', 'dfs and similar', 'dsu', 'graphs', 'trees', 'string suffix structures', 'strings', 'data structures', 'shortest paths', 'hashing', 'expression parsing', 'constructive algorithms', 'math', 'matrices', 'binary search', 'bitmasks', 'number theory', 'probabilities', 'geometry', 'dp', 'graph matchings', 'flows', 'two pointers', 'games', 'fft', '2-sat', 'ternary search', 'chinese remainder theorem'])


In [17]:
SCORE_LIMIT = 2.0

def calc_reversed_tfidf(tfidf):
    reversed_tfidf = defaultdict(list)
    for tag in tfidf:
        for var, score in tfidf[tag]:
            if score > SCORE_LIMIT:
                reversed_tfidf[var].append({'score': score, 'tag': tag})
    return reversed_tfidf

def predict(x_test, reversed_tfidf):

    result = []
    for xc in x_test:
        tag_scores = defaultdict(float)
        for var in xc.split():
            for score in reversed_tfidf[var]:
                if var == 'lca' and score['tag'] in ('probabilities', 'dsu'):
                    score['score'] = 800
                if var in ('unionsets', 'findset', 'makeset') and score['tag'] == 'dsu':
                    score['score'] = 800
                if var.startswith('dp') and score['tag'] == 'dp':
                    score['score'] = 800
                tag_scores[score['tag']] += score['score']
        tag_scores_items = list(tag_scores.items())
        tag_scores_items.sort(key=lambda x: -x[1])
        result.append(tag_scores_items)
    return result


reversed_tfidf = calc_reversed_tfidf(tfidf_scores)

In [18]:
tfidf_results = predict(x, reversed_tfidf)

In [19]:
def finalize_score(x, tfidf_results):
    for xc, extrac, tfidfc in zip(x, extra, tfidf_results):
        extra_tags = apply_detectors(xc, extrac, all_tags)
        for new_tag in extra_tags:
            for ind, tag in enumerate(tfidf_results):
                if tag == new_tag:
                    tfidfc[ind][1] = 1000.
                    if ind != 0:
                        tfidfc[ind], tfidfc[0] = tfidfc[0], tfidfc[ind]
                    break
            else:
                tfidfc.append((new_tag, 1000.))
                if len(tfidfc) > 1:
                    tfidfc[0], tfidfc[-1] = tfidfc[-1], tfidfc[0]
                    

In [20]:
with open('tags_by_solution_info.json', 'w') as out:
    json.dump(dict(zip(solution_info, tfidf_results)), out)

In [21]:
for key in reversed_tfidf:
    print(key)
    for item in sorted(reversed_tfidf[key], key = lambda x: -x['score']):
        print(item)
    print('-' * 20)

fac
{'score': 162.74110684957316, 'tag': 'combinatorics'}
{'score': 143.8435739503741, 'tag': 'math'}
{'score': 109.3092589267397, 'tag': 'dp'}
{'score': 72.55170473849368, 'tag': 'number theory'}
{'score': 20.824340175195836, 'tag': 'fft'}
{'score': 19.193964787813954, 'tag': 'trees'}
{'score': 18.378777094123016, 'tag': 'data structures'}
{'score': 16.52607779027997, 'tag': 'bitmasks'}
{'score': 14.228730653514592, 'tag': 'probabilities'}
{'score': 9.115280574907786, 'tag': 'strings'}
{'score': 8.151876936909401, 'tag': 'binary search'}
{'score': 6.447393577373799, 'tag': 'constructive algorithms'}
{'score': 5.928637772297747, 'tag': 'graphs'}
{'score': 5.558097911529138, 'tag': 'shortest paths'}
{'score': 4.5205863013770315, 'tag': 'dfs and similar'}
{'score': 3.9277225241472573, 'tag': 'matrices'}
{'score': 3.557182663378648, 'tag': 'hashing'}
{'score': 2.3714551089190987, 'tag': 'dsu'}
{'score': 2.075023220304211, 'tag': 'chinese remainder theorem'}
{'score': 2.0009152481504895, '

maxdeg
{'score': 8.317766166719343, 'tag': 'combinatorics'}
{'score': 4.1588830833596715, 'tag': 'dfs and similar'}
{'score': 4.1588830833596715, 'tag': 'trees'}
{'score': 4.1588830833596715, 'tag': 'dp'}
{'score': 2.772588722239781, 'tag': 'graphs'}
--------------------
tcaf
{'score': 8.317766166719343, 'tag': 'combinatorics'}
{'score': 5.545177444479562, 'tag': 'dp'}
{'score': 2.772588722239781, 'tag': 'math'}
--------------------
dfs2
{'score': 199.44016063307734, 'tag': 'trees'}
{'score': 180.23804451085547, 'tag': 'dfs and similar'}
{'score': 102.44765362935429, 'tag': 'dp'}
{'score': 93.24663965412296, 'tag': 'graphs'}
{'score': 83.68194923718289, 'tag': 'data structures'}
{'score': 29.53052706675033, 'tag': 'dsu'}
{'score': 25.89376264966285, 'tag': 'binary search'}
{'score': 22.111527655891873, 'tag': 'constructive algorithms'}
{'score': 17.238263336994653, 'tag': 'math'}
{'score': 11.45580791382556, 'tag': 'probabilities'}
{'score': 9.855631570307068, 'tag': 'shortest paths'}


{'score': 2.2384631517416906, 'tag': 'constructive algorithms'}
--------------------
chai
{'score': 8.769340779467576, 'tag': 'math'}
{'score': 5.011051873981472, 'tag': 'combinatorics'}
{'score': 2.505525936990736, 'tag': 'number theory'}
--------------------
inifc
{'score': 5.011051873981472, 'tag': 'combinatorics'}
{'score': 3.758288905486104, 'tag': 'dp'}
{'score': 2.505525936990736, 'tag': 'trees'}
{'score': 2.505525936990736, 'tag': 'math'}
{'score': 2.505525936990736, 'tag': 'number theory'}
--------------------
tmp5
{'score': 6.26381484247684, 'tag': 'fft'}
{'score': 5.011051873981472, 'tag': 'combinatorics'}
{'score': 5.011051873981472, 'tag': 'number theory'}
{'score': 2.505525936990736, 'tag': 'data structures'}
{'score': 2.505525936990736, 'tag': 'math'}
--------------------
paw
{'score': 5.011051873981472, 'tag': 'combinatorics'}
{'score': 3.758288905486104, 'tag': 'math'}
{'score': 3.758288905486104, 'tag': 'dp'}
{'score': 2.505525936990736, 'tag': 'number theory'}
------

{'score': 2.0399163355260588, 'tag': 'strings'}
{'score': 2.0399163355260588, 'tag': 'geometry'}
--------------------
digit
{'score': 14.16314118571591, 'tag': 'dp'}
{'score': 5.901308827381629, 'tag': 'math'}
{'score': 4.327626473413194, 'tag': 'bitmasks'}
{'score': 3.7374955906750316, 'tag': 'combinatorics'}
{'score': 3.5407852964289774, 'tag': 'data structures'}
{'score': 2.557233825198706, 'tag': 'strings'}
{'score': 2.557233825198706, 'tag': 'constructive algorithms'}
{'score': 2.557233825198706, 'tag': 'number theory'}
{'score': 2.3605235309526513, 'tag': 'dfs and similar'}
--------------------
newl
{'score': 11.211710848522, 'tag': 'math'}
{'score': 9.343092373768334, 'tag': 'dp'}
{'score': 7.474473899014667, 'tag': 'data structures'}
{'score': 5.605855424261, 'tag': 'graphs'}
{'score': 3.7372369495073334, 'tag': 'combinatorics'}
{'score': 3.7372369495073334, 'tag': 'dfs and similar'}
{'score': 3.7372369495073334, 'tag': 'trees'}
--------------------
fuc
{'score': 6.540164661637

--------------------
workg
{'score': 4.621335122841447, 'tag': 'dp'}
{'score': 3.080890081894298, 'tag': 'combinatorics'}
--------------------
workf
{'score': 4.621335122841447, 'tag': 'dp'}
{'score': 3.080890081894298, 'tag': 'combinatorics'}
--------------------
rozy
{'score': 6.161780163788596, 'tag': 'math'}
{'score': 3.080890081894298, 'tag': 'combinatorics'}
{'score': 3.080890081894298, 'tag': 'data structures'}
{'score': 3.080890081894298, 'tag': 'constructive algorithms'}
{'score': 3.080890081894298, 'tag': 'dp'}
{'score': 3.080890081894298, 'tag': 'fft'}
--------------------
pwl
{'score': 3.080890081894298, 'tag': 'combinatorics'}
{'score': 3.080890081894298, 'tag': 'math'}
{'score': 3.080890081894298, 'tag': 'dp'}
--------------------
gca
{'score': 3.080890081894298, 'tag': 'combinatorics'}
{'score': 3.080890081894298, 'tag': 'shortest paths'}
{'score': 3.080890081894298, 'tag': 'math'}
{'score': 3.080890081894298, 'tag': 'bitmasks'}
{'score': 3.080890081894298, 'tag': 'numbe

...

isbigger
{'score': 3.332204510175204, 'tag': 'binary search'}
--------------------
lastk
{'score': 3.332204510175204, 'tag': 'binary search'}
--------------------
btotal
{'score': 3.332204510175204, 'tag': 'binary search'}
--------------------
nhp
{'score': 3.332204510175204, 'tag': 'binary search'}
--------------------
rside
{'score': 3.332204510175204, 'tag': 'binary search'}
--------------------
price2
{'score': 3.332204510175204, 'tag': 'binary search'}
--------------------
att1
{'score': 3.332204510175204, 'tag': 'binary search'}
--------------------
answ1
{'score': 3.332204510175204, 'tag': 'binary search'}
--------------------
ingame
{'score': 3.332204510175204, 'tag': 'binary search'}
--------------------
newind
{'score': 3.332204510175204, 'tag': 'binary search'}
--------------------
prva
{'score': 3.332204510175204, 'tag': 'binary search'}
--------------------
pitaj
{'score': 3.332204510175204, 'tag': 'binary search'}
--------------------
solvable
{'score': 3.120771545364969,

shortdis
{'score': 13.328818040700815, 'tag': 'geometry'}
--------------------
equal3
{'score': 13.328818040700815, 'tag': 'geometry'}
--------------------
less3
{'score': 13.328818040700815, 'tag': 'geometry'}
--------------------
planoint
{'score': 13.328818040700815, 'tag': 'geometry'}
--------------------
sameside
{'score': 13.328818040700815, 'tag': 'geometry'}
--------------------
mirrors
{'score': 13.328818040700815, 'tag': 'geometry'}
--------------------
fastmax
{'score': 13.328818040700815, 'tag': 'geometry'}
--------------------
m2x
{'score': 13.328818040700815, 'tag': 'geometry'}
--------------------
m2y
{'score': 13.328818040700815, 'tag': 'geometry'}
--------------------
myline
{'score': 13.328818040700815, 'tag': 'geometry'}
--------------------
ternaryx
{'score': 13.195286648076292, 'tag': 'geometry'}
{'score': 13.195286648076292, 'tag': 'ternary search'}
--------------------
interseccion
{'score': 12.059366184187725, 'tag': 'geometry'}
--------------------
east
{'score

--------------------
pref0
{'score': 3.080890081894298, 'tag': 'dp'}
--------------------
isspecial
{'score': 3.080890081894298, 'tag': 'dp'}
--------------------
nxtpos
{'score': 3.080890081894298, 'tag': 'dp'}
--------------------
ansidx
{'score': 3.080890081894298, 'tag': 'dp'}
--------------------
ri1
{'score': 3.080890081894298, 'tag': 'dp'}
--------------------
can3
{'score': 3.080890081894298, 'tag': 'dp'}
--------------------
tmpsum
{'score': 3.080890081894298, 'tag': 'dp'}
--------------------
pck
{'score': 3.080890081894298, 'tag': 'dp'}
--------------------
jm
{'score': 3.080890081894298, 'tag': 'dp'}
--------------------
lpt
{'score': 3.080890081894298, 'tag': 'dp'}
--------------------
faktorial
{'score': 3.080890081894298, 'tag': 'dp'}
--------------------
fstpos
{'score': 3.080890081894298, 'tag': 'dp'}
--------------------
rating
{'score': 3.080890081894298, 'tag': 'dp'}
--------------------
lone
{'score': 3.080890081894298, 'tag': 'dp'}
--------------------
testcases
{

faj
--------------------
preva
--------------------
ertek
--------------------
logt
--------------------
rhl
--------------------
sdat
--------------------
gemacht
--------------------
countc
--------------------
pom1
--------------------
nulls
--------------------
tii
--------------------
allequal
--------------------
pek
--------------------
colorn
--------------------
indiam
--------------------
vacio
--------------------
getcut
--------------------
vind
--------------------
freev
--------------------
iot
--------------------
ccp
--------------------
mymp
--------------------
shen
--------------------
checkup
--------------------
mleft
--------------------
psr
--------------------
notin
--------------------
lwr
--------------------
rok
--------------------
revnode
--------------------
lowp
--------------------
kub
--------------------
grph
--------------------
getletter
--------------------
daan
--------------------
newq
--------------------
dw1
--------------------
dw2
------------

rfrom
--------------------
bcmp
--------------------
qnode
--------------------
buildhei
--------------------
queryrmq
--------------------
maxgood
--------------------
cmpo
--------------------
computeans
--------------------
itres
--------------------
excl
--------------------
tocol
--------------------
postsum
--------------------
chkr
--------------------
getmin1
--------------------
getvar
--------------------
pvert
--------------------
cret
--------------------
strongconnect
--------------------
iscircle
--------------------
addcol
--------------------
addrow
--------------------
vat
--------------------
przerob
--------------------
needp
--------------------
primefac
--------------------
rowcnt
--------------------
appoint
--------------------
getmex
--------------------
makefa
--------------------
rtmp
--------------------
rvs
--------------------
getrnd
--------------------
rech
--------------------
etour
--------------------
badl
--------------------
printline
---------------

transform by task

In [22]:
meta

{'source_codes/28/C/242747.cpp': {'variables': ['N',
   'M',
   'a',
   'cap',
   'i',
   'j',
   'k'],
  'function_names': []},
 'source_codes/1009/F/40364617.cpp': {'variables': ['n',
   'adj',
   'cnt',
   'lev',
   'ans',
   'u',
   'v'],
  'function_names': ['dfs']},
 'source_codes/946/D/36032178.cpp': {'variables': ['mp', 'pre', 'ori'],
  'function_names': []},
 'source_codes/86/D/27685223.cpp': {'variables': ['arr',
   'cnt1',
   'cnt2',
   'bno',
   'l',
   'r',
   'ind',
   'i',
   'j',
   't1',
   't2',
   't3',
   't4',
   'n',
   'm',
   'cul',
   'cur',
   'blok',
   'l1',
   'r1',
   'ind1'],
  'function_names': []},
 'source_codes/13/E/14714925.cpp': {'variables': ['a',
   'nxt',
   'td',
   'n',
   'q',
   't',
   'x',
   'v'],
  'function_names': ['build']},
 'source_codes/559/B/12188858.cpp': {'variables': ['a', 'b'],
  'function_names': []},
 'source_codes/961/G/37033692.cpp': {'variables': ['fact', 'inv'],
  'function_names': ['power', 'ncr', 'S']},
 'source_codes/3

In [23]:
tasks

[{'index': 'G',
  'name': 'Most Dangerous Shark',
  'rating': 2900,
  'tags': ['data structures', 'dp', 'two pointers'],
  'points': 3500.0,
  'contestId': 1131,
  'type': 'PROGRAMMING'},
 {'index': 'F',
  'name': 'Asya And Kittens',
  'rating': 1700,
  'tags': ['constructive algorithms', 'dsu'],
  'points': 3000.0,
  'contestId': 1131,
  'type': 'PROGRAMMING'},
 {'index': 'E',
  'name': 'String Multiplication',
  'rating': 2200,
  'tags': ['dp', 'greedy', 'strings'],
  'points': 2500.0,
  'contestId': 1131,
  'type': 'PROGRAMMING'},
 {'index': 'D',
  'name': 'Gourmet choice',
  'rating': 2000,
  'tags': ['dfs and similar', 'dp', 'dsu', 'graphs', 'greedy'],
  'points': 2000.0,
  'contestId': 1131,
  'type': 'PROGRAMMING'},
 {'index': 'C',
  'name': 'Birthday',
  'rating': 1200,
  'tags': ['binary search', 'greedy', 'sortings'],
  'points': 1500.0,
  'contestId': 1131,
  'type': 'PROGRAMMING'},
 {'index': 'B',
  'name': 'Draw!',
  'rating': 1300,
  'tags': ['greedy', 'implementation'],


In [24]:
tasks_dict = {
        (str(value['contestId']), value['index']): value
        for value in tasks
    }
print(tasks_dict)

{('1131', 'G'): {'index': 'G', 'name': 'Most Dangerous Shark', 'rating': 2900, 'tags': ['data structures', 'dp', 'two pointers'], 'points': 3500.0, 'contestId': 1131, 'type': 'PROGRAMMING'}, ('1131', 'F'): {'index': 'F', 'name': 'Asya And Kittens', 'rating': 1700, 'tags': ['constructive algorithms', 'dsu'], 'points': 3000.0, 'contestId': 1131, 'type': 'PROGRAMMING'}, ('1131', 'E'): {'index': 'E', 'name': 'String Multiplication', 'rating': 2200, 'tags': ['dp', 'greedy', 'strings'], 'points': 2500.0, 'contestId': 1131, 'type': 'PROGRAMMING'}, ('1131', 'D'): {'index': 'D', 'name': 'Gourmet choice', 'rating': 2000, 'tags': ['dfs and similar', 'dp', 'dsu', 'graphs', 'greedy'], 'points': 2000.0, 'contestId': 1131, 'type': 'PROGRAMMING'}, ('1131', 'C'): {'index': 'C', 'name': 'Birthday', 'rating': 1200, 'tags': ['binary search', 'greedy', 'sortings'], 'points': 1500.0, 'contestId': 1131, 'type': 'PROGRAMMING'}, ('1131', 'B'): {'index': 'B', 'name': 'Draw!', 'rating': 1300, 'tags': ['greedy', 

In [25]:
def group_meta_by_tasks(tasks, meta, all_tags):
    tasks_dict = {
        (str(value['contestId']), value['index']): value
        for value in tasks
    }
    groupped_by_task = defaultdict(list)
    for solution_path, value in meta.items():
        _, task_contest, task_index, _ = solution_path.split('/')
        task = tasks_dict[task_contest, task_index]
        tags = task['tags']
        task_x = []
        if not tags:
            continue
        for item_key in 'variables', 'function_names':
            for word in value[item_key]:
                if word in good_words:
                    task_x.append(normalize(word))
        groupped_by_task[(task_contest, task_index)] += task_x
    
    x = []
    y = []
    task_info = []
    for task_key, values in groupped_by_task.items():
        x.append(' '.join(values))
        task = tasks_dict[task_key]
        tags = task['tags']
        y.append([int(tag in tags) for tag in all_tags])
        task_info.append(task_key)
        
    return x, y, task_info

In [53]:
x, y, tasks_info = group_meta_by_tasks(tasks, meta, all_tags)
TRAIN_PART = 0.8
border = int(TRAIN_PART * len(x))
x_train = x[:border]
y_train = y[:border]
tasks_info_train = tasks_info[:border]

x_test = x[border:]
y_test = y[border:]
tasks_info_test = tasks_info[border:]


In [54]:
tfidf_scores = process(x_train, y_train, all_tags)
print(tfidf_scores.keys())

dict_keys(['combinatorics', 'dp', 'probabilities', 'data structures', 'dsu', 'trees', 'math', 'two pointers', 'hashing', 'strings', 'number theory', 'flows', 'graph matchings', 'binary search', 'dfs and similar', 'graphs', 'shortest paths', 'chinese remainder theorem', 'constructive algorithms', 'bitmasks', 'games', 'geometry', 'matrices', 'string suffix structures', 'ternary search', 'fft', 'expression parsing', '2-sat'])


In [55]:
reversed_tfidf = calc_reversed_tfidf(tfidf_scores)
tfidf_results = predict(x_test, reversed_tfidf)

In [56]:
def make_predict(results, all_tags, score_limit=30, cut_items=5):
    y_predicted = []
    for result in results:
        filtered = [item[0] for item in result[:cut_items] if item[1] > score_limit]
        yc = [int(tag in filtered) for tag in all_tags]
        y_predicted.append(yc)
    return y_predicted

In [60]:
tasks_info_train[0]

('28', 'C')

In [58]:
tfidf_results[0]

[('dfs and similar', 118.0726737668681),
 ('graphs', 106.48051567523011),
 ('data structures', 101.95897378052615),
 ('trees', 101.29284841473316),
 ('dp', 99.88379303876793),
 ('flows', 43.422967140024504),
 ('math', 39.9802080072828),
 ('binary search', 34.902907264385995),
 ('dsu', 33.7491737905718),
 ('constructive algorithms', 31.434507020300394),
 ('strings', 28.995783684091375),
 ('shortest paths', 25.8210273613211),
 ('string suffix structures', 17.05642511614028),
 ('hashing', 16.110866367697533),
 ('geometry', 16.002207380349475),
 ('bitmasks', 15.777412588940877),
 ('number theory', 13.601942865071742),
 ('combinatorics', 13.550306191373755),
 ('two pointers', 9.310116907743947),
 ('graph matchings', 8.946440466035199),
 ('probabilities', 8.873705177693449),
 ('games', 4.0368085029671015),
 ('2-sat', 2.9094115336699833),
 ('matrices', 2.836676245328234)]

In [31]:
y_test_predicted = make_predict(tfidf_results, all_tags)

In [32]:
from sklearn.metrics import jaccard_similarity_score
import numpy as np
def calculate_score(y_true, y_pred):
    return jaccard_similarity_score(np.array(y_true), np.array(y_pred))

In [33]:
calculate_score(y_test, y_test_predicted)

0.2472334368530021

In [34]:
best_score = -1
best_score_limit = None
best_cut_items = None
for score_limit in range(20, 150, 10):
    for cut_items in range(3, 8):
        _y_test_predicted = make_predict(tfidf_results, all_tags, score_limit=score_limit, cut_items=cut_items)
        score = calculate_score(y_test, _y_test_predicted)
        if score > best_score:
            best_score_limit = score_limit
            best_cut_items = cut_items
            best_score = score
print(best_score, best_score_limit, best_cut_items)

0.34094202898550724 130 3


In [35]:
mx = {}
for key in tfidf_scores:
    mx[key] = tfidf_scores[key][0][1]
def make_predict2(results, all_tags, mx, score_limit=0.1, cut_items=5):
    y_predicted = []
    for result in results:
        res = [(x[0], x[1] / mx[x[0]]) for x in result]
        res.sort(key=lambda x: -x[1])
        filtered = [item[0] for item in res[:cut_items] if item[1] > score_limit]
        yc = [int(tag in filtered) for tag in all_tags]
        y_predicted.append(yc)
    return y_predicted

In [36]:
best_score = -1
best_score_limit = None
best_cut_items = None
for score_limit in range(10, 100, 5):
    for cut_items in range(3, 8):
        _y_test_predicted = make_predict2(tfidf_results, all_tags, mx, score_limit=score_limit/100, cut_items=cut_items)
        score = calculate_score(y_test, _y_test_predicted)
        if score > best_score:
            best_score_limit = score_limit/100
            best_cut_items = cut_items
            best_score = score
print(best_score, best_score_limit, best_cut_items)

0.35114389233954457 0.95 3


In [37]:
import gensim.summarization.bm25 as bm25


def train_bm25(x_train, y_train, all_tags):
    tag_meta = defaultdict(list)
    for cx, cy in zip(x_train, y_train):
        for tag, cy_item in zip(all_tags, cy):
            if cy_item:
                tag_meta[tag] += cx.split(' ')
    keys = tag_meta.keys()
    corpus = tag_meta.values()
    bm25_object = bm25.BM25(corpus)
    return bm25_object, keys

In [38]:
bm25_object, keys = train_bm25(x_train, y_train, all_tags)

In [39]:
def predict_bm25(x_test, bm25_object, keys):
    result = []
    for cx in x_test:
        scores = bm25_object.get_scores(cx)
        tag_scores_items = sorted(zip(keys, scores), key=lambda x: -x[1])
        result.append(tag_scores_items)
    return result

In [40]:
bm25_results = predict_bm25(x_test, bm25_object, keys)

In [41]:
best_score = -1
best_cut_items = None
for cut_items in range(1, 8):
    _y_test_predicted = make_predict(tfidf_results, all_tags, score_limit=0, cut_items=cut_items)
    score = calculate_score(y_test, _y_test_predicted)
    if score > best_score:
        best_cut_items = cut_items
        best_score = score
print(best_score, best_score_limit, best_cut_items)

0.19126811594202894 0.95 1


Этот метод работает хуже

In [42]:
vectorizer = TfidfVectorizer()  # parameters?
vectorizer.fit(x_train)
vectorizer.fit(x_test)
x_train_transformed = vectorizer.transform(x_train)
x_test_transformed = vectorizer.transform(x_test)
x_train_inp = lil_matrix(x_train_transformed).toarray()
y_train_inp = lil_matrix(y_train).toarray()
x_test_inp = lil_matrix(x_test_transformed).toarray()
y_test_inp = lil_matrix(y_test).toarray()

In [45]:
len(x_train_inp)

3677

In [48]:
from skmultilearn.embedding import SKLearnEmbedder, EmbeddingClassifier
from sklearn.manifold import SpectralEmbedding
from sklearn.ensemble import RandomForestRegressor
from skmultilearn.adapt import MLkNN


for k_ in (3, 5, 7, 9):
    classifier_new = MLkNN(k=k_)
    clf.fit(x_train_inp[:n], y_train_inp[:n])
    predictions = clf.predict(x_test_inp)
    print('k = {}; Accuracy = {}'.format(k_, jaccard_similarity_score(y_test_inp, predictions)))

k = 3; Accuracy = 0.40137681159420296
k = 5; Accuracy = 0.4018840579710145
k = 7; Accuracy = 0.39201086956521736
k = 9; Accuracy = 0.4065036231884058


In [49]:
from skmultilearn.embedding import SKLearnEmbedder, EmbeddingClassifier
from sklearn.manifold import SpectralEmbedding
from sklearn.ensemble import RandomForestRegressor
from skmultilearn.adapt import MLkNN

best_score = -1
best_n_components = None
best_n_estimators = None
best_k = None
for n_components_ in (3, 5, 10):
    for n_estimators_ in (3, 5, 10):
        for k_ in (3, 5, 7, 9):
            clf = EmbeddingClassifier(
                SKLearnEmbedder(SpectralEmbedding(n_components=n_components_)),
                RandomForestRegressor(n_estimators=n_estimators_),
                MLkNN(k=k_),
            )

            clf.fit(x_train_inp[:n], y_train_inp[:n])
            predictions = clf.predict(x_test_inp)
            score = jaccard_similarity_score(y_test_inp, predictions)
            print('n_components: {}; n_estimators: {}; k: {}; score = {}'.format(
                n_components_,
                n_estimators_,
                k_,
                score,
            ) )
            if score > best_score:
                best_score = score
                best_n_components = n_components_
                best_n_estimators = n_estimators_
                best_k = k_
print('Best: n_components: {}; n_estimators: {}; k: {}; score = {}'.format(
    n_components_,
    n_estimators_,
    k_,
    score,
))

n_components: 3; n_estimators: 3; k: 3; score = 0.3938043478260869
n_components: 3; n_estimators: 3; k: 5; score = 0.3990760869565217
n_components: 3; n_estimators: 3; k: 7; score = 0.4121557971014493
n_components: 3; n_estimators: 3; k: 9; score = 0.4092934782608696
n_components: 3; n_estimators: 5; k: 3; score = 0.40603260869565216
n_components: 3; n_estimators: 5; k: 5; score = 0.3902355072463768
n_components: 3; n_estimators: 5; k: 7; score = 0.4067753623188406
n_components: 3; n_estimators: 5; k: 9; score = 0.42112318840579704
n_components: 3; n_estimators: 10; k: 3; score = 0.393713768115942
n_components: 3; n_estimators: 10; k: 5; score = 0.40246376811594203
n_components: 3; n_estimators: 10; k: 7; score = 0.40994565217391304
n_components: 3; n_estimators: 10; k: 9; score = 0.4263768115942029
n_components: 5; n_estimators: 3; k: 3; score = 0.4056702898550725
n_components: 5; n_estimators: 3; k: 5; score = 0.37425724637681157
n_components: 5; n_estimators: 3; k: 7; score = 0.4084